In [211]:
import torch, torchvision
import numpy as np
from tqdm import tqdm
import plotly.express as px
import torch.nn.functional as F
from plotly.subplots import make_subplots
import plotly.graph_objects as go

In [173]:
def generate_example(dpl, mu, a, b, xmin, xmax, ymin, ymax, npix):
    xaxis = np.linspace(xmin, xmax, npix)
    yaxis = np.linspace(ymin, ymax, npix)
    norm_x = np.linspace(-1, 1, len(xaxis))
    norm_y = np.linspace(-1, 1, len(yaxis))
    xv, yv = np.meshgrid(xaxis, yaxis, indexing='ij')
    zz = - ((dpl/(2*mu))*((xv**2)/2 - (a+b)*xv + (a*b + (b**2)/2)))
    # Set boundary conditions
    zz[xv>=(2*a+b)]=0
    zz[xv<=b]=0
    return zz

In [174]:
def generate_dataset(n_samples, xmin=0, xmax=10, ymin=0, ymax=10, npix=64):
    # flow parameters
    dpl = (np.random.rand(n_samples)-0.5)*4 # change this parameter
#     dpl = np.random.rand(n_samples)*2
    mu = 1 # assume mu constant as same fluid
    
    # height parameters
    b = (xmax/2)*np.random.rand(n_samples) # just setting a constraint
    a_max = (xmax - b)/2 - 2*xmax/npix # have at least one boundary pixel at the top 
    a = a_max*np.random.rand(n_samples) + xmax/npix # add this to prevent a thickness of one pixel
    
    # generate samples
    samples = np.zeros((n_samples, 1, npix, npix)) # the 1 holds for the number of varaibles (u, v, w, p)?
    for i in tqdm(range(n_samples)):
        samples[i, 0] = generate_example(dpl[i], mu, a[i], b[i], xmin, xmax, ymin, ymax, npix)
    
    # normalize samples (would have to store those means for evaluation)
    # different normalizations, for each sample or across all dataset
    # are those values normally distributed initially?
    means = samples.mean(axis=(-1, -2, 0), keepdims=True)
    stds = samples.std(axis=(-1, -2, 0), keepdims=True)
    norm_samples = (samples-means)/stds
    
    # segmentation_maps = torch.randint(3, (num_images, 1, num_elem, num_elem), dtype=torch.float)
    segmentation_maps = np.zeros((n_samples, 1, npix, npix))
    segmentation_maps[samples!=0] = 2 # points where there is some flow
    
    # find the edges by computing the gradient
    edges_top = np.minimum(segmentation_maps[:, 0, :-1, :] - segmentation_maps[:, 0, 1:, :], np.zeros_like(segmentation_maps[:, 0, :-1, :]))/(-2)
    edges_bottom = np.minimum(segmentation_maps[:, 0, 1:, :] - segmentation_maps[:, 0, :-1, :], np.zeros_like(segmentation_maps[:, 0, :-1, :]))/(-2) # divide by -2 to get the desired 1 for bounday points
    
    # add edges to top and bottom
    segmentation_maps[:, 0, :-1, :] += edges_top
    segmentation_maps[:, 0, 1:, :] += edges_bottom
    
    # simply add edges on the side for now - will be change if we want none 90-degrees rotations
    segmentation_maps[:, :, :, 0][segmentation_maps[:, :, :, 0]==2] = 1
    segmentation_maps[:, :, :, -1][segmentation_maps[:, :, :, -1]==2] = 1
    
    return norm_samples, segmentation_maps


In [175]:
samples, segmentation_maps = generate_dataset(500)

100%|██████████| 500/500 [00:00<00:00, 5382.70it/s]


In [176]:
i = iter(range(20))

In [197]:
c = next(i)
img1 = np.expand_dims(samples[c, 0], axis=0)
img2 = np.expand_dims(segmentation_maps[c, 0], axis=0)
exs = np.concatenate([img1, img2], axis=0)
fig = px.imshow(exs, facet_col=0, facet_col_wrap=2)
fig.for_each_annotation(lambda a: a.update(text="Flow field" if a.text.split("=")[1]=="0" else "Segmentation map"))
fig

StopIteration: 

In [ ]:
# with rotations

In [2330]:
n_samples=10
xmin=0
xmax=10
ymin=0
ymax=10
npix=64

In [2432]:
dpl = np.ones(n_samples) #(np.random.rand(n_samples)-0.5)*2 # change this parameter
mu = 1 # assume mu constant as same fluid

# height parameters
# b = (xmax/2)*np.random.rand(n_samples) # just setting a constraint
b = (xmax/1.1)*np.random.rand(n_samples) # just setting a constraint
a_max = (xmax - b)/2 #- 2*xmax/npix # have at least one boundary pixel at the top 
a = a_max*np.random.rand(n_samples) + 3*xmax/npix # add this to prevent a thickness of one pixel

angles = (np.random.rand(n_samples)-0.5)*180


# generate samples
samples = np.zeros((n_samples, 1, npix, npix)) # the 1 holds for the number of varaibles (u, v, w, p)?
xaxis = np.linspace(xmin, xmax, npix)
yaxis = np.linspace(ymin, ymax, npix)
norm_x = np.linspace(-1, 1, len(xaxis))
norm_y = np.linspace(-1, 1, len(yaxis))
xv, yv = np.meshgrid(xaxis, yaxis, indexing='ij')

for i in tqdm(range(n_samples)):
    # rotation
    if angles[i]>90 or angles[i]<-90:
        angles[i] = angles[i]%180
    if angles[i]<0:
        b[i] = xmax*np.cos(angles[i]*np.pi/180)/2 - b[i]
    if angles[i]>0:
        b[i] = xmax*np.cos(angles[i]*np.pi/180)/2 + b[i]
    
    xv_rot = xv*np.cos(angles[i]*np.pi/180) + yv*np.sin(angles[i]*np.pi/180)    
    vel = - ((dpl[i]/(2*mu))*((xv_rot**2)/2 - (a[i]+b[i])*xv_rot + (a[i]*b[i] + (b[i]**2)/2)))
    
    # Set boundary conditions
#     print("thickness:", 2*a*64/10, "distance from bottom", b*64/10)
    vel[xv_rot>=(2*a[i]+b[i])]=0
    vel[xv_rot<=b[i]]=0
    samples[i, 0] = vel

velocities = np.zeros((samples.shape[0], 2, samples.shape[2], samples.shape[3]))
velocities[:, [0]] = np.reshape(np.cos(angles*np.pi/180), (-1, 1, 1, 1))*samples # u
velocities[:, [1]] = np.reshape(np.sin(angles*np.pi/180), (-1, 1, 1, 1))*samples # v
# px.imshow(vel)


100%|██████████| 10/10 [00:00<00:00, 4798.43it/s]


In [2433]:
# segmentation_maps = torch.randint(3, (num_images, 1, num_elem, num_elem), dtype=torch.float)
segmentation_maps = np.zeros((n_samples, 1, npix, npix))
segmentation_maps[samples!=0] = 2 # points where there is some flow

# find the edges by computing the gradient
edges_top = np.minimum(segmentation_maps[:, 0, :-1, :] - segmentation_maps[:, 0, 1:, :], np.zeros_like(segmentation_maps[:, 0, :-1, :]))/(-2)
edges_bottom = np.minimum(segmentation_maps[:, 0, 1:, :] - segmentation_maps[:, 0, :-1, :], np.zeros_like(segmentation_maps[:, 0, :-1, :]))/(-2) # divide by -2 to get the desired 1 for bounday points
edges_left = np.minimum(segmentation_maps[:, 0, :, :-1] - segmentation_maps[:, 0, :, 1:], np.zeros_like(segmentation_maps[:, 0, :, :-1]))/(-2)
edges_right = np.minimum(segmentation_maps[:, 0, :, 1:] - segmentation_maps[:, 0, :, :-1], np.zeros_like(segmentation_maps[:, 0, :, :-1]))/(-2) # divide by -2 to get the desired 1 for bounday points

# add edges to top and bottom
segmentation_maps[:, 0, :-1, :] += 3*edges_top 
segmentation_maps[:, 0, :-1, :] += 3*edges_bottom
segmentation_maps[:, 0, :, :-1] += 3*edges_left
segmentation_maps[:, 0, :, :-1] += 3*edges_right
segmentation_maps[segmentation_maps>2]=1


# simply add edges on the side for now - will be change if we want none 90-degrees rotations
segmentation_maps[:, :, :, 0][segmentation_maps[:, :, :, 0]==2] = 1
segmentation_maps[:, :, :, -1][segmentation_maps[:, :, :, -1]==2] = 1
segmentation_maps[:, :, 0, :][segmentation_maps[:, :, 0, :]==2] = 1
segmentation_maps[:, :, -1, :][segmentation_maps[:, :, -1, :]==2] = 1


In [2434]:
fig = px.imshow(samples.squeeze(), facet_col=0, facet_col_wrap=5)
fig.for_each_annotation(lambda a: a.update(text="Flow field"))
fig

In [2435]:
fig = px.imshow(segmentation_maps[:,0].squeeze(), facet_col=0, facet_col_wrap=5)
fig.for_each_annotation(lambda a: a.update(text="Flow field"))
fig

In [2479]:
def generate_example(dpl, mu, a, b, xmin, xmax, ymin, ymax, npix, angle):
    # rotation
#     print(angle)
    if angle>90 or angle<-90:
        angle = angle%180
    if angle<0:
        b = xmax*np.cos(angle*np.pi/180)/2 - b
    if angle>0:
        b = xmax*np.cos(angle*np.pi/180)/2 + b
    
    xv_rot = xv*np.cos(angle*np.pi/180) + yv*np.sin(angle*np.pi/180)    
    vel = - ((dpl/(2*mu))*((xv_rot**2)/2 - (a+b)*xv_rot + (a*b + (b**2)/2)))
    
    # Set boundary conditions
    vel[xv_rot>=(2*a+b)]=0
    vel[xv_rot<=b]=0
    return vel

In [2480]:
def generate_dataset(n_samples, xmin=0, xmax=10, ymin=0, ymax=10, npix=64):
    # flow parameters
#     dpl = np.abs((np.random.rand(n_samples)-0.5)*4) # change this parameter
    dpl = np.random.rand(n_samples)/2 + 1
    mu = 1 # assume mu constant as same fluid
    
    # height parameters
    b = (xmax/2)*np.random.rand(n_samples) # just setting a constraint
    a_max = (xmax - b)/2 #- 2*xmax/npix # have at least one boundary pixel at the top 
    a = a_max*(np.random.rand(n_samples)/8)*0 + 6*xmax/npix # add this to prevent a thickness of one pixel
    
    # angle parameter
    angles = (np.random.rand(n_samples)-0.5)*180
    
    # generate samples
    samples = np.zeros((n_samples, 1, npix, npix)) # the 1 holds for the number of varaibles (u, v, w, p)?
    for i in tqdm(range(n_samples)):
        samples[i, 0] = generate_example(dpl[i], mu, a[i], b[i], xmin, xmax, ymin, ymax, npix, angles[i])
    
    velocities = np.zeros((samples.shape[0], 2, samples.shape[2], samples.shape[3]))
    velocities[:, [0]] = np.reshape(np.cos(angles*np.pi/180), (-1, 1, 1, 1))*samples # u
    velocities[:, [1]] = np.reshape(np.sin(angles*np.pi/180), (-1, 1, 1, 1))*samples # v
    
    # normalize samples (would have to store those means for evaluation)
    # different normalizations, for each sample or across all dataset
    # are those values normally distributed initially?
    means = velocities.mean(axis=(-1, -2, 0), keepdims=True)
    stds = velocities.std(axis=(-1, -2, 0), keepdims=True)
    norm_velocities = (velocities-means)/stds
    
    # segmentation_maps = torch.randint(3, (num_images, 1, num_elem, num_elem), dtype=torch.float)
    segmentation_maps = np.zeros((n_samples, 1, npix, npix))
    segmentation_maps[samples!=0] = 2 # points where there is some flow

    # find the edges by computing the gradient
    edges_top = np.minimum(segmentation_maps[:, 0, :-1, :] - segmentation_maps[:, 0, 1:, :], np.zeros_like(segmentation_maps[:, 0, :-1, :]))/(-2)
    edges_bottom = np.minimum(segmentation_maps[:, 0, 1:, :] - segmentation_maps[:, 0, :-1, :], np.zeros_like(segmentation_maps[:, 0, :-1, :]))/(-2) # divide by -2 to get the desired 1 for bounday points
    edges_left = np.minimum(segmentation_maps[:, 0, :, :-1] - segmentation_maps[:, 0, :, 1:], np.zeros_like(segmentation_maps[:, 0, :, :-1]))/(-2)
    edges_right = np.minimum(segmentation_maps[:, 0, :, 1:] - segmentation_maps[:, 0, :, :-1], np.zeros_like(segmentation_maps[:, 0, :, :-1]))/(-2) # divide by -2 to get the desired 1 for bounday points

    # add edges to top and bottom
    segmentation_maps[:, 0, :-1, :] += 3*edges_top 
    segmentation_maps[:, 0, :-1, :] += 3*edges_bottom
    segmentation_maps[:, 0, :, :-1] += 3*edges_left
    segmentation_maps[:, 0, :, :-1] += 3*edges_right
    segmentation_maps[segmentation_maps>2]=1

    # simply add edges on the side for now - will be change if we want none 90-degrees rotations
    segmentation_maps[:, :, :, 0][segmentation_maps[:, :, :, 0]==2] = 1
    segmentation_maps[:, :, :, -1][segmentation_maps[:, :, :, -1]==2] = 1
    segmentation_maps[:, :, 0, :][segmentation_maps[:, :, 0, :]==2] = 1
    segmentation_maps[:, :, -1, :][segmentation_maps[:, :, -1, :]==2] = 1
    
    return norm_velocities, segmentation_maps


In [2485]:
n_samples = 10
samples, segs = generate_dataset(n_samples, xmin=0, xmax=10, ymin=0, ymax=10, npix=64)

100%|██████████| 10/10 [00:00<00:00, 2965.43it/s]


In [2486]:
fig = px.imshow(samples[:,0].squeeze(), facet_col=0, facet_col_wrap=5)
fig.for_each_annotation(lambda a: a.update(text="Flow field"))
fig

In [2487]:
fig = px.imshow(segs[:,0].squeeze(), facet_col=0, facet_col_wrap=5)
fig.for_each_annotation(lambda a: a.update(text="Flow field"))
fig

In [ ]:
dp = 1
L = 1
mu = 2
H = 1

b = 0.5
a = 1
xaxis = np.linspace(0, 7, 16)
yaxis = np.linspace(0, 10, 16)
norm_x = np.linspace(-1, 1, len(xaxis))
norm_y = np.linspace(-1, 1, len(yaxis))
xv, yv = np.meshgrid(xaxis, yaxis, indexing='ij')
zz = - ((dp/(2*mu*L))*((xv**2)/2 - (a+b)*xv + (a*b + (b**2)/2)))

# Set boundary conditions
zz[xv>=(2*a+b)]=0
zz[xv<=b]=0

px.imshow(zz)

In [11]:
# Normalize the data
norm = lambda a : 2 * (a - np.min(a))/(np.max(a) - np.min(a)) - 1
xv = norm(xv)
yv = norm(yv)

In [ ]:
zz_batched = torch.tensor(zz).unsqueeze(0).repeat((3, 1, 1, 1))
zz_batched.shape

In [ ]:
# segmentation_maps = torch.randint(3, (num_images, 1, num_elem, num_elem), dtype=torch.float)
segmentation_maps = torch.zeros((num_images, 1, 64, 64), dtype=torch.float)
segmentation_maps[zz_batched!=0] = 2

In [ ]:
px.imshow(segmentation_maps[0, 0])

In [ ]:
edges_top = torch.minimum(segmentation_maps[0, 0, :-1, :] - segmentation_maps[0, 0, 1:, :], torch.zeros_like(segmentation_maps[0, 0, :-1, :]))/(-2)
# px.imshow(edges_top)
edges_bottom = torch.minimum(segmentation_maps[0, 0, 1:, :] - segmentation_maps[0, 0, :-1, :], torch.zeros_like(segmentation_maps[0, 0, :-1, :]))/(-2)
# px.imshow(edges_bottom)
# px.imshow(segmentation_maps[0, 0, :-1, :] - segmentation_maps[0, 0, 1:, :])

In [ ]:
segmentation_maps[0, 0, :-1, :] += edges_top
segmentation_maps[0, 0, 1:, :] += edges_bottom

In [ ]:
px.imshow(segmentation_maps[0, 0])

In [ ]:
px.imshow(zz, x=norm_y, y=norm_x)

In [ ]:
class PointPooling2D(torch.nn.Module):
    """
    Local pooling operation.
    """

    def __init__(self, interpolation='bilinear'):
        super().__init__()
        self.interp_mode = interpolation

    def forward(self, latent_space, vertices):
        grid = 2 * vertices - 1
        grid = grid.unsqueeze(1).unsqueeze(1).flip(dims=(-1,))

        interp = F.grid_sample(latent_space, grid, mode=self.interp_mode, padding_mode="border", align_corners=True)
        interp = interp.squeeze(2).squeeze(2)
        out = torch.transpose(interp, 1, 2)

        return out

In [199]:
num_features = 20
num_elem = 4
num_images = 3
latent_space = torch.arange(num_images*num_features*num_elem*num_elem, dtype=torch.float)
latent_space = latent_space.reshape((num_images, num_features, num_elem, num_elem))
segmentation_maps = torch.randint(3, (num_images, 1, num_elem, num_elem), dtype=torch.float)

In [200]:
pts = torch.tensor([[1, -1], [1, 1], [-1, 1], [-1, -1]], dtype=torch.float)
pts = pts.repeat((num_images, 1, 1, 1))
print(pts.shape)
pts = pts.flip(dims=(-1,))

torch.Size([3, 1, 4, 2])


In [ ]:
interp_features = F.grid_sample(latent_space, pts, align_corners=True)
interp_features = (interp_features.squeeze())
# batch_size x number_of_features
interp_labels = F.grid_sample(segmentation_maps, pts, align_corners=True)
interp_labels = (interp_labels.squeeze())

In [ ]:
interp_features.shape # num_images, number_of_features, num_points

In [ ]:
pts.squeeze().permute(0, 2, 1).shape

In [ ]:
feature_vector = torch.cat([pts.squeeze().permute(0, 2, 1).flip(dims=(-1,)), interp_features], dim=1) # reflip points to have
# our coordinate system

In [ ]:
feature_vector.shape # num_images, num_features, num_points

In [ ]:
# Permute so that I can change the batch size to have all of them together
feature_vector = feature_vector.permute(0, 2, 1) # num_images, num_points, num_features
feature_vector = feature_vector.reshape(-1, 22) # (num_images x num_points), num_features
interp_labels = interp_labels.reshape(-1, 1) # (num_images x num_points), 1

In [ ]:
bckg_points = feature_vector[(interp_labels == 0).squeeze()]
boundary_points = feature_vector[(interp_labels == 1).squeeze()]
interior_points = feature_vector[(interp_labels == 2).squeeze()]

In [ ]:
bckg_points.shape, boundary_points.shape, interior_points.shape

In [ ]:
latent_space = torch.arange(2*4*4, dtype=torch.float)
latent_space = latent_space.reshape((1, 2, 4, 4))
segmentation_maps = torch.randint(3, (1, 1, 4, 4), dtype=torch.float)

In [ ]:
pts = torch.tensor([[1, -1], [1, 1], [-1, 1], [-1, -1]], dtype=torch.float)
print(pts, pts.shape)
pts = torch.unsqueeze(torch.unsqueeze(pts, 0), 0)
pts = pts.flip(dims=(-1,))
pts, pts.shape

In [ ]:
interp_features = F.grid_sample(latent_space, pts, align_corners=True)
interp_features = (interp_features.squeeze()).T
# batch_size x number_of_features
interp_labels = F.grid_sample(segmentation_maps, pts, align_corners=True)
interp_labels = (interp_labels.squeeze()).T

In [ ]:
latent_space, interp_labels

In [ ]:
feature_vector = torch.cat([pts.flip(dims=(-1,)).squeeze(), interp], dim=-1)

In [ ]:
feature_vector

In [ ]:
background_points = feature_vector[interp_labels==0]
boundary_points = feature_vector[interp_labels==1]
interior_points = feature_vector[interp_labels==2]

In [ ]:
interior_points